# Setup

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!git clone https://github.com/kubapok/cnlps-caiccaic.git

Cloning into 'cnlps-caiccaic'...
remote: Enumerating objects: 73, done.
remote: Counting objects: 100% (73/73), done.
remote: Compressing objects: 100% (56/56), done.
remote: Total 73 (delta 32), reused 41 (delta 11), pack-reused 0
Unpacking objects: 100% (73/73), 1.89 MiB | 4.48 MiB/s, done.


In [ ]:
!pip install -Uq datasets transformers peft bitsandbytes loralib accelerate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.6/474.6 kB 10.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 78.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.2/92.2 MB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.5/227.5 kB 27.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 23.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 16.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 75.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 27.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 126.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

# Create dataset

In [ ]:
!cat cnlps-caiccaic/train/in.tsv  cnlps-caiccaic/dev-A/in.tsv > in.tsv
!cat cnlps-caiccaic/train/expected.tsv  cnlps-caiccaic/dev-A/expected.tsv > expected.tsv

In [ ]:
import csv
from datasets import Dataset, DatasetDict

with open('in.tsv', encoding='utf-8') as train_f_in, open('expected.tsv', encoding='utf-8') as train_f_exp:
  train_list_in = list(csv.reader(train_f_in, delimiter='\t'))
  train_list_exp = train_f_exp.readlines()

with open('cnlps-caiccaic/test-A/in.tsv', encoding='utf-8') as test_f_in:
  test_list_in = list(csv.reader(test_f_in, delimiter='\t'))

train_data = Dataset.from_list([{'text': f'{in_[3]} language: {in_[1]}', 'intent': exp.strip().replace('}', ']').replace('{', '[').replace('\t', '|')} for in_, exp in zip(train_list_in, train_list_exp)])
test_data = Dataset.from_list([{'text': f'{in_[3]} language: {in_[1]}', 'intent': ''} for in_ in test_list_in])
dataset = DatasetDict({'train': train_data, 'test': test_data})

In [ ]:
dataset['train'][600]

{'text': "don't alert me when an event in my calendar in location kenner begins language: en-US",
 'intent': "Calendar|NotNotifyOnEventInLocation|['location': 'kenner']"}

# Define training components

In [ ]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

model_name = 'google/flan-t5-large'
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForSeq2SeqLM.from_pretrained(model_name, device_map='auto')

In [ ]:
def preprocess_function(sample):
    inputs = ['Create an annotation based on the following data. ' + item for item in sample['text']]
    model_inputs = tokenizer(inputs, padding=True, truncation=True)
    labels = tokenizer(text_target=sample['intent'], padding=True, truncation=True)
    labels['input_ids'] = [[(l if l != tokenizer.pad_token_id else -100) for l in label] for label in labels['input_ids']]
    model_inputs['labels'] = labels['input_ids']
    return model_inputs

tokenized_dataset = dataset.map(preprocess_function, batched=True, remove_columns=['text', 'intent'])

In [ ]:
from transformers import DataCollatorForSeq2Seq

data_collator = DataCollatorForSeq2Seq(
    tokenizer,
    model=model
)

# Training

In [ ]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

output_dir='flan-t5_large'

training_args = Seq2SeqTrainingArguments(
    output_dir=output_dir,
	  auto_find_batch_size=True,
    num_train_epochs=1,
    logging_dir=f'{output_dir}/logs',
    save_steps=3000
)

trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset['train']
)
model.config.use_cache = False 

In [ ]:
trainer.train()

TrainOutput(global_step=12874, training_loss=0.06059208474804456, metrics={'train_runtime': 12136.5406, 'train_samples_per_second': 4.243, 'train_steps_per_second': 1.061, 'total_flos': 2.330193322605773e+16, 'train_loss': 0.06059208474804456, 'epoch': 1.0})

# Save the model

In [ ]:
trainer.model.save_pretrained('results_v2')
tokenizer.save_pretrained('results_v2')

In [ ]:
!rm -r /content/drive/MyDrive/caiccaic; mkdir /content/drive/MyDrive/caiccaic
!cp -r results_v2 /content/drive/MyDrive/caiccaic

In [ ]:
# from google.colab import runtime
# runtime.unassign()

# Inference

In [ ]:
!cp -r /content/drive/MyDrive/results_v2 .

In [ ]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer
import torch

model = AutoModelForSeq2SeqLM.from_pretrained('results_v2', device_map={'':0})
tokenizer = AutoTokenizer.from_pretrained('results_v2')
model.eval()

T5ForConditionalGeneration(
  (shared): Embedding(32128, 1024)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 1024)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=1024, out_features=1024, bias=False)
              (k): Linear(in_features=1024, out_features=1024, bias=False)
              (v): Linear(in_features=1024, out_features=1024, bias=False)
              (o): Linear(in_features=1024, out_features=1024, bias=False)
              (relative_attention_bias): Embedding(32, 16)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=1024, out_features=2816, bias=False)
              (wi_1): Linear(in_features=1024, out_features=2816, bias=False)
       

In [ ]:
import numpy as np
from datasets import load_from_disk
from tqdm import tqdm

def evaluate_peft_model(sample):
    outputs = model.generate(input_ids=torch.tensor(sample['input_ids']).unsqueeze(0).cuda(), max_new_tokens=512) 
    prediction = tokenizer.decode(outputs[0].detach().cpu().numpy(), skip_special_tokens=True)
    return prediction

test_dataset = tokenized_dataset['test']

predictions, references = [], []
i = 0
for sample in tqdm(test_dataset):
  p = evaluate_peft_model(sample)
  if i % 100 == 0:
    print('\n', p)
  predictions.append(p)
  i += 1

  0%|          | 0/10358 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1255: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  warnings.warn(
  0%|          | 1/10358 [00:03<9:53:16,  3.44s/it]


 Airconditioner|SetTemperatureOnDevice|['device_name': 'firmes stet']


  1%|          | 101/10358 [02:47<4:55:07,  1.73s/it]


 Calendar|AddEventWithName|['event_name':'meeting with conremarch fisht']


  2%|▏         | 201/10358 [04:57<3:07:32,  1.11s/it]

...

 98%|█████████▊| 10201/10358 [5:57:18<05:42,  2.18s/it]


 Websearch|SearchImagesWithTextOnEngineWithWidthAndWithHeightAndWithCondition|['img_query': 'rita maestre']


 99%|█████████▉| 10301/10358 [6:00:14<01:35,  1.67s/it]


 Yelp|SearchByQueryInLocation|['location': 'aulesti', 'query': 'cerveceras artesanales y pubs']


100%|██████████| 10358/10358 [6:01:25<00:00,  2.09s/it]


In [ ]:
# format predictions to target shape
predictions = [prediction.replace('|', '\t', 3).replace('[', '{').replace(']', '}').strip() for prediction in predictions]

In [ ]:
with open('/content/cnlps-caiccaic/test-A/out_v2.tsv', 'w', encoding='utf-8') as out:
  for pred in predictions:
    out.write(pred + '\n')

In [ ]:
import locale
locale.getpreferredencoding = lambda: "UTF-8"

In [ ]:
!cp /content/cnlps-caiccaic/test-A/out_v2.tsv /content/drive/MyDrive/

In [ ]:
from google.colab import runtime
runtime.unassign()